# 1. Imports

In [30]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from pandas import DataFrame, Series
import seaborn as sns
from tqdm.notebook import tqdm
from typing import Optional

import category_encoders
from category_encoders import WOEEncoder
from optuna import Trial
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, make_scorer
from sklearn.model_selection import cross_val_score, KFold, StratifiedKFold
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import Pipeline

from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier

from utils.eda import summary

# 2. Notebook settings

In [44]:
import warnings
warnings.filterwarnings("ignore")
pd.options.display.float_format = '{:,.4f}'.format

# 3. Data Load

In [3]:
test_df = pd.read_csv('test.csv')
train_df = pd.read_csv('train.csv')
submission_df = pd.read_csv('sample_submission.csv')

# 4. Data Cleaning 

In [4]:
cat_cols = [column for column in train_df.columns if train_df[column].dtype == 'object']
num_cols = train_df.select_dtypes(include=[np.number]).columns.tolist()

num_cols.remove('id')
num_cols.remove('CustomerId')
num_cols.remove('IsActiveMember')
num_cols.remove('HasCrCard')
num_cols.remove('Exited')
cat_cols.remove('Surname')
cat_cols.append('IsActiveMember')
cat_cols.append('HasCrCard')

train_df['HasCrCard'] = train_df['HasCrCard'].astype(bool)
train_df['IsActiveMember'] = train_df['IsActiveMember'].astype(bool)
test_df['HasCrCard'] = test_df['HasCrCard'].astype(bool)
test_df['IsActiveMember'] = test_df['IsActiveMember'].astype(bool)
train_df.head()

id  CustomerId         Surname  CreditScore Geography Gender   Age  Tenure  \
0   0    15674932  Okwudilichukwu          668    France   Male 33.00       3   
1   1    15749177   Okwudiliolisa          627    France   Male 33.00       1   
2   2    15694510           Hsueh          678    France   Male 40.00      10   
3   3    15741417             Kao          581    France   Male 34.00       2   
4   4    15766172       Chiemenam          716     Spain   Male 33.00       5   

     Balance  NumOfProducts  HasCrCard  IsActiveMember  EstimatedSalary  \
0       0.00              2       True           False       181,449.97   
1       0.00              2       True            True        49,503.50   
2       0.00              2       True           False       184,866.69   
3 148,882.54              1       True            True        84,560.88   
4       0.00              2       True            True        15,068.83   

   Exited  
0       0  
1       0  
2       0  
3       0  
4       0

# 5. Model Setup

In [25]:
def instantiate_woe_encoder(trial : Trial) -> WOEEncoder:
  params = {
    'sigma': trial.suggest_float('sigma', 0.001, 5),
    'regularization': trial.suggest_float('regularization', 0, 5),
    'randomized': trial.suggest_categorical('randomized', [True, False])
  }
  return WOEEncoder(**params)

def instantiate_robust_scaler(trial : Trial) -> RobustScaler:
  params = {
    'with_centering': trial.suggest_categorical(
      'with_centering', [True, False]
    ),
    'with_scaling': trial.suggest_categorical(
      'with_scaling', [True, False]
    )
  }
  return RobustScaler(**params)

def instantiate_catboost(trial : Trial) -> CatBoostClassifier:
  params = {
    'n_estimators': trial.suggest_int('n_estimators', 50, 200, 10),
    'max_depth': trial.suggest_int('max_depth', 2, 10),
    'random_state': 42
  }
  return CatBoostClassifier(**params)

def instantiate_logistic(trial : Trial) -> LogisticRegression:
  params = {
        'tol' : trial.suggest_uniform('tol' , 1e-6 , 1e-3),
        'C' : trial.suggest_loguniform("C", 1e-2, 1),
  }
  return LogisticRegression(**params)

def instantiate_xgboost(trial : Trial) -> XGBClassifier:
  params = {
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 2, 10),
        "subsample": trial.suggest_float("subsample", 0.05, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.05, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 20),
  }
  return XGBClassifier(**params)

def instantiate_numerical_pipeline(trial : Trial) -> Pipeline:
  pipeline = Pipeline([
    ('scaler', instantiate_robust_scaler(trial))
  ])
  return pipeline

def instantiate_categorical_pipeline(trial : Trial) -> Pipeline:
  pipeline = Pipeline([
    ('encoder', instantiate_woe_encoder(trial))
  ])
  return pipeline

In [21]:
from sklearn.compose import ColumnTransformer

def instantiate_processor(trial : Trial, numerical_columns : list[str], categorical_columns : list[str]) -> ColumnTransformer:
  
  numerical_pipeline = instantiate_numerical_pipeline(trial)
  categorical_pipeline = instantiate_categorical_pipeline(trial)
  
  processor = ColumnTransformer([
    ('numerical_pipeline', numerical_pipeline, numerical_columns),
    ('categorical_pipeline', categorical_pipeline, categorical_columns)
  ])
  
  return processor

def instantiate_model(trial : Trial, numerical_columns : list[str], categorical_columns : list[str], algo: str) -> Pipeline:
  
  processor = instantiate_processor(
    trial, numerical_columns, categorical_columns
  )
  
  if algo == 'cat':
    model = instantiate_catboost(trial)
  elif algo == 'log':
    model = instantiate_logistic(trial)
  elif algo == 'xgb':
    model = instantiate_xgboost(trial)
  
  model = Pipeline([
    ('processor', processor),
    ('extra_trees', model)
  ])
  
  return model

In [27]:
def objective(trial : Trial, X : DataFrame, y : np.ndarray | Series, algo: str, numerical_columns : Optional[list[str]]=None, categorical_columns : Optional[list[str]]=None, random_state : int=42, ) -> float:
  if numerical_columns is None:
    numerical_columns = [
      *X.select_dtypes(exclude=['object', 'category']).columns
    ]
  
  if categorical_columns is None:
    categorical_columns = [
      *X.select_dtypes(include=['object', 'category']).columns
    ]
  
  model = instantiate_model(trial, numerical_columns, categorical_columns, algo)
  
  skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=random_state)
  roc_auc_scorer = make_scorer(roc_auc_score, needs_proba=True)
  scores = cross_val_score(model, X, y, scoring=roc_auc_scorer, cv=skf)
  
  return np.min([np.mean(scores), np.median([scores])])

# 6. Training

## Logistic Regression

In [11]:
from optuna import create_study

study_log = create_study(study_name='optimization', direction='maximize')

study_log.optimize(lambda trial: objective(trial, train_df[cat_cols + num_cols], train_df['Exited'], algo='log'), n_trials=100)

[I 2024-01-11 19:17:05,718] A new study created in memory with name: optimization
[I 2024-01-11 19:17:06,846] Trial 0 finished with value: 0.8177820153015325 and parameters: {'with_centering': True, 'with_scaling': True, 'sigma': 3.7127175369763297, 'regularization': 1.0176760558785887, 'randomized': False, 'tol': 0.00024826354460997694, 'C': 0.03599113061478923}. Best is trial 0 with value: 0.8177820153015325.
[I 2024-01-11 19:17:08,446] Trial 1 finished with value: 0.6136275945832402 and parameters: {'with_centering': True, 'with_scaling': False, 'sigma': 0.7781680548066527, 'regularization': 3.4843130648737115, 'randomized': False, 'tol': 0.00038912962203274833, 'C': 0.03688336577540392}. Best is trial 0 with value: 0.8177820153015325.
[I 2024-01-11 19:17:09,763] Trial 2 finished with value: 0.7138149012764249 and parameters: {'with_centering': False, 'with_scaling': False, 'sigma': 3.903022659312896, 'regularization': 0.8295220332369424, 'randomized': False, 'tol': 0.00076436917077

## Catboost

In [19]:
from optuna import create_study

study_cat = create_study(study_name='optimization', direction='maximize')

study_cat.optimize(lambda trial: objective(trial, train_df[cat_cols + num_cols], train_df['Exited'], algo='cat'), n_trials=100)

[I 2024-01-11 19:25:34,809] A new study created in memory with name: optimization


Learning rate set to 0.5
0:	learn: 0.4728497	total: 67.8ms	remaining: 8.75s
1:	learn: 0.3905705	total: 73.2ms	remaining: 4.68s
2:	learn: 0.3560609	total: 78ms	remaining: 3.3s
3:	learn: 0.3388416	total: 83.1ms	remaining: 2.62s
4:	learn: 0.3307047	total: 88.2ms	remaining: 2.21s
5:	learn: 0.3258626	total: 93.8ms	remaining: 1.94s
6:	learn: 0.3233169	total: 99.3ms	remaining: 1.75s
7:	learn: 0.3212651	total: 105ms	remaining: 1.61s
8:	learn: 0.3207284	total: 111ms	remaining: 1.49s
9:	learn: 0.3196712	total: 116ms	remaining: 1.39s
10:	learn: 0.3190752	total: 121ms	remaining: 1.31s
11:	learn: 0.3185958	total: 126ms	remaining: 1.24s
12:	learn: 0.3182373	total: 132ms	remaining: 1.19s
13:	learn: 0.3178859	total: 137ms	remaining: 1.14s
14:	learn: 0.3171891	total: 142ms	remaining: 1.09s
15:	learn: 0.3169753	total: 148ms	remaining: 1.05s
16:	learn: 0.3164269	total: 153ms	remaining: 1.02s
17:	learn: 0.3160504	total: 158ms	remaining: 981ms
18:	learn: 0.3157166	total: 163ms	remaining: 953ms
19:	learn: 0

[I 2024-01-11 19:25:39,334] Trial 0 finished with value: 0.8859996921394631 and parameters: {'with_centering': True, 'with_scaling': True, 'sigma': 0.39867194366016034, 'regularization': 1.072414014725488, 'randomized': True, 'n_estimators': 130, 'max_depth': 8}. Best is trial 0 with value: 0.8859996921394631.


119:	learn: 0.2885159	total: 606ms	remaining: 50.5ms
120:	learn: 0.2883400	total: 611ms	remaining: 45.4ms
121:	learn: 0.2880804	total: 616ms	remaining: 40.4ms
122:	learn: 0.2878454	total: 622ms	remaining: 35.4ms
123:	learn: 0.2874835	total: 627ms	remaining: 30.3ms
124:	learn: 0.2872294	total: 632ms	remaining: 25.3ms
125:	learn: 0.2870588	total: 637ms	remaining: 20.2ms
126:	learn: 0.2868971	total: 642ms	remaining: 15.2ms
127:	learn: 0.2865272	total: 647ms	remaining: 10.1ms
128:	learn: 0.2863138	total: 651ms	remaining: 5.05ms
129:	learn: 0.2861032	total: 656ms	remaining: 0us
Learning rate set to 0.399367
0:	learn: 0.5122228	total: 3.25ms	remaining: 583ms
1:	learn: 0.4308454	total: 6.36ms	remaining: 566ms
2:	learn: 0.3887661	total: 10.6ms	remaining: 626ms
3:	learn: 0.3615751	total: 13.7ms	remaining: 604ms
4:	learn: 0.3487829	total: 16.9ms	remaining: 592ms
5:	learn: 0.3379528	total: 20ms	remaining: 581ms
6:	learn: 0.3333429	total: 24.3ms	remaining: 600ms
7:	learn: 0.3290171	total: 27.6ms	r

[I 2024-01-11 19:25:43,092] Trial 1 finished with value: 0.8888541175730572 and parameters: {'with_centering': True, 'with_scaling': True, 'sigma': 1.2998325174072944, 'regularization': 1.7345806244886792, 'randomized': False, 'n_estimators': 180, 'max_depth': 5}. Best is trial 1 with value: 0.8888541175730572.


...

137:	learn: 0.3139219	total: 397ms	remaining: 5.75ms
138:	learn: 0.3138685	total: 400ms	remaining: 2.88ms
139:	learn: 0.3138360	total: 404ms	remaining: 0us
Learning rate set to 0.444917
0:	learn: 0.4998347	total: 2.84ms	remaining: 451ms
1:	learn: 0.4243240	total: 5.74ms	remaining: 454ms
2:	learn: 0.3836213	total: 8.6ms	remaining: 450ms
3:	learn: 0.3613554	total: 14.9ms	remaining: 580ms
4:	learn: 0.3487775	total: 17.7ms	remaining: 548ms
5:	learn: 0.3384605	total: 20.7ms	remaining: 531ms
6:	learn: 0.3339898	total: 23.6ms	remaining: 517ms
7:	learn: 0.3304319	total: 31.2ms	remaining: 593ms
8:	learn: 0.3281711	total: 33.9ms	remaining: 569ms
9:	learn: 0.3263475	total: 37.3ms	remaining: 560ms
10:	learn: 0.3253614	total: 40.1ms	remaining: 543ms
11:	learn: 0.3247566	total: 43ms	remaining: 531ms
12:	learn: 0.3240952	total: 46.4ms	remaining: 525ms
13:	learn: 0.3233648	total: 49.2ms	remaining: 513ms
14:	learn: 0.3230309	total: 52.7ms	remaining: 510ms
15:	learn: 0.3225094	total: 55.4ms	remaining: 4

[I 2024-01-11 19:30:35,359] Trial 98 finished with value: 0.8892539505650984 and parameters: {'with_centering': False, 'with_scaling': False, 'sigma': 4.437713437062441, 'regularization': 2.572553026798982, 'randomized': False, 'n_estimators': 160, 'max_depth': 4}. Best is trial 65 with value: 0.8895212854286466.


113:	learn: 0.3130377	total: 399ms	remaining: 161ms
114:	learn: 0.3129753	total: 402ms	remaining: 157ms
115:	learn: 0.3129280	total: 407ms	remaining: 154ms
116:	learn: 0.3129028	total: 410ms	remaining: 151ms
117:	learn: 0.3128230	total: 413ms	remaining: 147ms
118:	learn: 0.3127559	total: 416ms	remaining: 143ms
119:	learn: 0.3127077	total: 419ms	remaining: 140ms
120:	learn: 0.3126825	total: 423ms	remaining: 136ms
121:	learn: 0.3126323	total: 426ms	remaining: 133ms
122:	learn: 0.3125758	total: 429ms	remaining: 129ms
123:	learn: 0.3125644	total: 432ms	remaining: 125ms
124:	learn: 0.3125044	total: 436ms	remaining: 122ms
125:	learn: 0.3124535	total: 439ms	remaining: 119ms
126:	learn: 0.3124382	total: 442ms	remaining: 115ms
127:	learn: 0.3123711	total: 445ms	remaining: 111ms
128:	learn: 0.3123217	total: 448ms	remaining: 108ms
129:	learn: 0.3122800	total: 452ms	remaining: 104ms
130:	learn: 0.3122069	total: 455ms	remaining: 101ms
131:	learn: 0.3121818	total: 458ms	remaining: 97.2ms
132:	learn:

[I 2024-01-11 19:30:36,992] Trial 99 finished with value: 0.887530614188883 and parameters: {'with_centering': False, 'with_scaling': False, 'sigma': 4.862086379637449, 'regularization': 2.4398544698778375, 'randomized': False, 'n_estimators': 60, 'max_depth': 2}. Best is trial 65 with value: 0.8895212854286466.


Learning rate set to 0.5
0:	learn: 0.5111081	total: 2.32ms	remaining: 137ms
1:	learn: 0.4401194	total: 4.59ms	remaining: 133ms
2:	learn: 0.3996209	total: 6.65ms	remaining: 126ms
3:	learn: 0.3788996	total: 8.78ms	remaining: 123ms
4:	learn: 0.3655916	total: 11.2ms	remaining: 124ms
5:	learn: 0.3556372	total: 13.4ms	remaining: 121ms
6:	learn: 0.3504185	total: 16.6ms	remaining: 126ms
7:	learn: 0.3418273	total: 19.3ms	remaining: 126ms
8:	learn: 0.3388903	total: 21.3ms	remaining: 121ms
9:	learn: 0.3365467	total: 23.3ms	remaining: 117ms
10:	learn: 0.3347718	total: 25.6ms	remaining: 114ms
11:	learn: 0.3338772	total: 27.7ms	remaining: 111ms
12:	learn: 0.3327304	total: 29.7ms	remaining: 107ms
13:	learn: 0.3314413	total: 33.1ms	remaining: 109ms
14:	learn: 0.3307546	total: 35.8ms	remaining: 107ms
15:	learn: 0.3297677	total: 37.8ms	remaining: 104ms
16:	learn: 0.3274532	total: 40ms	remaining: 101ms
17:	learn: 0.3269311	total: 42ms	remaining: 98ms
18:	learn: 0.3265283	total: 44.6ms	remaining: 96.2ms
1

## XGBooost

In [26]:
from optuna import create_study

study_xgb = create_study(study_name='optimization', direction='maximize')

study_xgb.optimize(lambda trial: objective(trial, train_df[cat_cols + num_cols], train_df['Exited'], algo='xgb'), n_trials=100)

[I 2024-01-11 19:32:36,696] A new study created in memory with name: optimization
[I 2024-01-11 19:32:38,793] Trial 0 finished with value: 0.8827795089980979 and parameters: {'with_centering': False, 'with_scaling': True, 'sigma': 1.4649158079141953, 'regularization': 0.8774550841281442, 'randomized': False, 'learning_rate': 0.0023423249748945486, 'max_depth': 5, 'subsample': 0.2060960737879816, 'colsample_bytree': 0.9702470851700724, 'min_child_weight': 16}. Best is trial 0 with value: 0.8827795089980979.
[I 2024-01-11 19:32:40,471] Trial 1 finished with value: 0.884670769808486 and parameters: {'with_centering': False, 'with_scaling': False, 'sigma': 1.0230533314204753, 'regularization': 3.4387281266714966, 'randomized': True, 'learning_rate': 0.04659997399719901, 'max_depth': 3, 'subsample': 0.7394187579007317, 'colsample_bytree': 0.5230256533888635, 'min_child_weight': 20}. Best is trial 1 with value: 0.884670769808486.
[I 2024-01-11 19:32:42,778] Trial 2 finished with value: 0.888

## LGMB

## Neural Net

# 7. Model Ensamble

In [47]:
md1 = instantiate_model(study_log.best_trial, num_cols, cat_cols, 'log')
md2 = instantiate_model(study_cat.best_trial, num_cols, cat_cols, 'cat')
md3 = instantiate_model(study_xgb.best_trial, num_cols, cat_cols, 'xgb')

md1_pred, md2_pred, md3_pred = list(), list(), list()
Y_test_list = list()

X = train_df[num_cols+cat_cols]
Y = train_df['Exited']

skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)

for i, (train_idx, test_idx) in enumerate(skf.split(X, Y)):

    X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
    Y_train, Y_test = Y.iloc[train_idx], Y.iloc[test_idx]
    
    md1.fit(X_train, Y_train)
    md1_pred.append(md1.predict_proba(X_test)[:, 1])

    md2.fit(X_train, Y_train)
    md2_pred.append(md2.predict_proba(X_test)[:, 1])

    md3.fit(X_train, Y_train)
    md3_pred.append(md3.predict_proba(X_test)[:, 1])

    Y_test_list.append(Y_test)

Learning rate set to 0.442565
0:	learn: 0.5106467	total: 4.75ms	remaining: 802ms
1:	learn: 0.4345723	total: 7.77ms	remaining: 652ms
2:	learn: 0.3964496	total: 12.4ms	remaining: 688ms
3:	learn: 0.3711702	total: 15.1ms	remaining: 628ms
4:	learn: 0.3572805	total: 19ms	remaining: 626ms
5:	learn: 0.3486433	total: 22.1ms	remaining: 603ms
6:	learn: 0.3433990	total: 25.2ms	remaining: 588ms
7:	learn: 0.3373916	total: 28.8ms	remaining: 583ms
8:	learn: 0.3339444	total: 31.4ms	remaining: 562ms
9:	learn: 0.3325113	total: 35.1ms	remaining: 562ms
10:	learn: 0.3309640	total: 37.7ms	remaining: 545ms
11:	learn: 0.3297671	total: 40.4ms	remaining: 533ms
12:	learn: 0.3287313	total: 43.7ms	remaining: 528ms
13:	learn: 0.3272711	total: 46.3ms	remaining: 516ms
14:	learn: 0.3266335	total: 49.1ms	remaining: 507ms
15:	learn: 0.3250205	total: 51.9ms	remaining: 499ms
16:	learn: 0.3245279	total: 54.5ms	remaining: 490ms
17:	learn: 0.3241703	total: 57.4ms	remaining: 485ms
18:	learn: 0.3238840	total: 60.4ms	remaining: 

In [53]:
w1_weights, w2_weights, w3_weights, scores = list(), list(), list(), list()

for i in tqdm(range(0, 1000)):
    
    w1 = np.random.random_sample(size = 1)[0]
    w2 = np.random.random_sample(size = 1)[0]
    w3 = np.random.random_sample(size = 1)[0]
    
    w1_weights.append(w1)
    w2_weights.append(w2)
    w3_weights.append(w3)

    scores_in = list()
    
    for j in range(0, 10):
        pred = w1*md3_pred[j] + w2*md2_pred[j] + w3*md1_pred[j]
        scores_in.append(roc_auc_score(Y_test_list[j], pred))
    
    scores.append(np.mean(scores_in))
    
results = pd.DataFrame()
results['w_log'] = w1_weights
results['w_cat'] = w2_weights
results['w_xgb'] = w3_weights
results['score'] = scores
results = results.sort_values(by = 'score', ascending = False).reset_index(drop = True)
results.head(10)

  0%|          | 0/1000 [00:00<?, ?it/s]

w_log  w_cat  w_xgb  score
0 0.9770 0.5826 0.0020 0.8900
1 0.9373 0.8826 0.0089 0.8900
2 0.8829 0.4920 0.0041 0.8900
3 0.8985 0.9407 0.0092 0.8900
4 0.9815 0.8364 0.0162 0.8900
5 0.2329 0.2138 0.0061 0.8900
6 0.8508 0.7384 0.0223 0.8900
7 0.7988 0.9054 0.0221 0.8900
8 0.3717 0.1682 0.0065 0.8899
9 0.7305 0.2426 0.0013 0.8899

In [54]:
md1_fit = md1.fit(X, Y)
md2_fit = md2.fit(X, Y)
md3_fit = md3.fit(X, Y)

md_pred_test = pd.DataFrame()
md_pred_test['LOG'] = md1_fit.predict_proba(test_df[cat_cols + num_cols])[:, 1]
md_pred_test['CAT'] = md2_fit.predict_proba(test_df[cat_cols + num_cols])[:, 1]
md_pred_test['XGB'] = md3_fit.predict_proba(test_df[cat_cols + num_cols])[:, 1]
md_pred_test

Learning rate set to 0.462931
0:	learn: 0.5045409	total: 5.39ms	remaining: 911ms
1:	learn: 0.4288921	total: 9.42ms	remaining: 791ms
2:	learn: 0.3918253	total: 12.6ms	remaining: 701ms
3:	learn: 0.3674477	total: 15.9ms	remaining: 662ms
4:	learn: 0.3542726	total: 18.9ms	remaining: 625ms
5:	learn: 0.3461904	total: 22ms	remaining: 602ms
6:	learn: 0.3414060	total: 25ms	remaining: 583ms
7:	learn: 0.3358566	total: 29.3ms	remaining: 593ms
8:	learn: 0.3325573	total: 32.2ms	remaining: 576ms
9:	learn: 0.3310740	total: 35.2ms	remaining: 563ms
10:	learn: 0.3300383	total: 38.6ms	remaining: 558ms
11:	learn: 0.3268012	total: 41.7ms	remaining: 549ms
12:	learn: 0.3259511	total: 44.7ms	remaining: 540ms
13:	learn: 0.3254398	total: 47.5ms	remaining: 529ms
14:	learn: 0.3250130	total: 50.3ms	remaining: 520ms
15:	learn: 0.3240116	total: 53.2ms	remaining: 512ms
16:	learn: 0.3237250	total: 55.9ms	remaining: 503ms
17:	learn: 0.3234304	total: 58.8ms	remaining: 496ms
18:	learn: 0.3231332	total: 61.9ms	remaining: 49

LOG    CAT    XGB
0      0.0242 0.0257 0.0210
1      0.5680 0.8337 0.8165
2      0.1509 0.0238 0.0303
3      0.2058 0.2352 0.2285
4      0.4191 0.4102 0.3335
...       ...    ...    ...
110018 0.0365 0.0371 0.0465
110019 0.1004 0.1413 0.0973
110020 0.0612 0.0195 0.0240
110021 0.0966 0.1407 0.1481
110022 0.3121 0.1883 0.1785

[110023 rows x 3 columns]

In [58]:
#test_probabilities = results['w_log'][0]*md_pred_test['LOG'] + results['w_cat'][0]*md_pred_test['CAT'] + results['w_xgb'][0]*md_pred_test['XGB']
test_probabilities = md_pred_test.mean(axis=1)
test_probabilities

0        0.0236
1        0.7394
2        0.0683
3        0.2231
4        0.3876
          ...  
110018   0.0400
110019   0.1130
110020   0.0349
110021   0.1285
110022   0.2263
Length: 110023, dtype: float64

In [ ]:
# Check for underfitting/overfitting by analyzing splits
# folds = range(1, kf.get_n_splits() + 1)
# plt.plot(folds, rmse_train, 'o-', color='green', label='train')
# plt.plot(folds, rmse_test, 'o-', color='red', label='test')
# plt.legend()
# plt.grid()
# plt.xlabel('Number of fold')
# plt.ylabel('mean squared error')
# plt.show()

In [59]:
sub = pd.DataFrame()
sub['id'] = test_df['id']
sub['Exited'] = test_probabilities
sub = sub.set_index('id')
sub.head()

Exited
id            
165034  0.0236
165035  0.7394
165036  0.0683
165037  0.2231
165038  0.3876

In [60]:
sub.to_csv('submission.csv')